# Prepare Dataset

In [ ]:
import sys, os
sys.path.append(os.path.abspath(".."))

import numpy as np
import pandas as pd
import glob
from dataset_helper import get_dataset, get_dataset_dir


# Amount of dataset lines that will be compiled and converted to dataset.jsonl. 
# If -1, use all lines.
# max_dataset=100
max_dataset=-1

output_onnx_name = "ml.onnx"
output_labels_name = "ml_labels.json"

# Load & process data

df, dir = get_dataset(inside_arena=True)

# df.to_csv(f"{get_dataset_dir()}/merged.csv", index=False)

if max_dataset>-1:
    df = df.sample(max_dataset)


d:\sumobot\sumobot_ml\venv\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


# Training

In [ ]:
import json
import tf2onnx

from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import train_test_split
from sklearn.impute import SimpleImputer
from sklearn.metrics import classification_report

import tensorflow as tf
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input, Dense, BatchNormalization
from tensorflow.keras.utils import to_categorical
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.callbacks import EarlyStopping
from tensorflow.keras.losses import CategoricalCrossentropy

# Load & process data
from dataset_helper import get_dataset

df, dir = get_dataset(inside_arena=True)

if max_dataset>-1:
    df = df.sample(max_dataset)

features = [
    "BotPosX", 
    "BotPosY", 
    "BotRot", 
    # "BotLinv",
    # "BotAngv", 
    # "BotIsDashActive",
    # "BotIsSkillActive", 
    # "BotIsOutFromArena",
    "EnemyBotPosX", 
    "EnemyBotPosY", 
    "EnemyBotRot",
    # "EnemyBotLinv",
    # "EnemyBotAngv", 
    # "EnemyBotIsDashActive",
    # "EnemyBotIsSkillActive", 
    # "EnemyBotIsOutFromArena",
]

X = df[features]
imputer = SimpleImputer(strategy="mean")
X = imputer.fit_transform(X)

# Encode label
le = LabelEncoder()
y_action = le.fit_transform(df["Name"])
y_duration = df["Duration"].values.astype("float32")

# One-hot encoding for action
y_action_cat = to_categorical(y_action)

# Split
X_train, X_test, y_action_train, y_action_test, y_duration_train, y_duration_test, df_train, df_val = train_test_split(
    X, y_action_cat, y_duration, df, test_size=0.2, random_state=42
)

# Build model
inputs = Input(shape=(X.shape[1], ))
x = Dense(256, activation='relu')(inputs)
x = BatchNormalization()(x)
x = Dense(128, activation='relu')(x)
x = Dense(64, activation='relu')(x)
x = Dense(32, activation='relu')(x)

output_action = Dense(y_action_cat.shape[1], activation='softmax', name="action")(x)
output_duration = Dense(1, activation='linear', name="duration")(x)

loss_action = CategoricalCrossentropy(label_smoothing=0.1)

# Compile model
model = Model(inputs=inputs, outputs=[output_action, output_duration])
model.compile(
    optimizer=Adam(learning_rate=0.0001),
    loss={"action": loss_action, "duration": "mae"},
    metrics={'action': 'accuracy', 'duration': 'mae'},
    weighted_metrics={'action': 'accuracy', 'duration': 'mae'}
)

# Early stopping
early_stop = EarlyStopping(
    monitor='val_loss',
    patience=10,
    min_delta=0.001,
    mode='min',
    restore_best_weights=True,
    verbose=1
)

# Train
model.fit(X_train, {"action": y_action_train, "duration": y_duration_train},
          validation_data=(X_test, {'action': y_action_test, 'duration': y_duration_test}),
          epochs=100,
          batch_size=512,
          callbacks=[early_stop],
          )

# Predict
pred_action_prob, pred_duration = model.predict(X_test)
pred_action = np.argmax(pred_action_prob, axis=1)
true_action = np.argmax(y_action_test, axis=1)

# Evaluation
print(classification_report(true_action, pred_action, target_names=le.classes_))

# Convert the model
spec = (tf.TensorSpec((None, X.shape[1]), tf.float32, name="input"),)
onnx_model, _ = tf2onnx.convert.from_keras(model, input_signature=spec, opset=13)

# Save to file
with open(output_onnx_name, "wb") as f:
    f.write(onnx_model.SerializeToString())

print(f"Model saved to {output_onnx_name}")

class_labels = le.classes_.tolist()

# Optional: Save labels to JSON
with open(output_labels_name, "w") as f:
    json.dump(class_labels, f)

print(f"Exported label encoder classes to {output_labels_name}")
print(class_labels)

# Testing

In [ ]:
import onnxruntime as ort
import numpy as np
import joblib

# Load ONNX session
session = ort.InferenceSession(output_onnx_name)

# Load label encoder
le = joblib.load(output_labels_name)

# 1 sample input (bisa ambil dari X_test atau manual)
sample = np.array([[
    -3.30086637,    # BotPosX
    2.01016259,   # BotPosY
    # 0,   # BotLinv
    # 0,   # BotAngv
    270,   # BotRot
    3.69913363,    # EnemyBotPosX
    2.01016259,   # EnemyBotPosY
    # 0,   # EnemyBotLinv
    # 0,  # EnemyBotAngv
    90   # EnemyBotRot
]], dtype=np.float32)

# Get input & output names
input_name = session.get_inputs()[0].name
output_names = [o.name for o in session.get_outputs()]  # action, duration

# Run inference
outputs = session.run(output_names, {input_name: sample})
pred_action_probs = outputs[0]
pred_duration = outputs[1]

# Decode predicted action
pred_action_index = np.argmax(pred_action_probs)
pred_action_label = le.inverse_transform([pred_action_index])[0]

print(f"Predicted action: {pred_action_label}")
print(f"Predicted duration: {pred_duration[0][0]:.4f}")
